In [8]:
import cudf
import cuspatial as csp
from shapely.geometry import Polygon
import pandas as pd
import geopandas as gpd
import hvplot.pandas
from holoviews import opts
import movingpandas as mpd

In [2]:
%%time
df = cudf.read_parquet("https://pydatatt.s3.amazonaws.com/Combined/ALL_GOM_cargo_2019-2021.parquet")
df

CPU times: user 6 s, sys: 1.61 s, total: 7.61 s
Wall time: 23.8 s


BaseDateTime         MMSI       LAT       LON  VesselName  \
0        2019-01-01 00:00:00  314263000.0  29.91651 -90.12085   LYCAVITOS   
1        2019-01-01 00:05:00  314263000.0  29.90751 -90.10366   LYCAVITOS   
2        2019-01-01 00:10:00  314263000.0  29.91338 -90.08699   LYCAVITOS   
3        2019-01-01 00:15:00  314263000.0  29.92024 -90.06981   LYCAVITOS   
4        2019-01-01 00:20:00  314263000.0  29.93362 -90.05813   LYCAVITOS   
...                      ...          ...       ...       ...         ...   
30775533 2021-12-31 23:35:00  477826600.0  27.46033 -88.52127  AMOY DREAM   
30775534 2021-12-31 23:40:00  477826600.0  27.47457 -88.53260  AMOY DREAM   
30775535 2021-12-31 23:45:00  477826600.0  27.48883 -88.54284  AMOY DREAM   
30775536 2021-12-31 23:50:00  477826600.0  27.50371 -88.55237  AMOY DREAM   
30775537 2021-12-31 23:55:00  477826600.0  27.52105 -88.56032  AMOY DREAM   

                 IMO   SOG  
0         IMO9368857  12.8  
1         IMO9368857  12.5  
2         IMO9368857  12.6  
3         IMO9368857  13.3  
4         IMO9368857  13.2  
...              ...   ...  
30775533  IMO9583615  12.9  
30775534  IMO9583615  13.0  
30775535  IMO9583615  13.0  
30775536  IMO9583615  13.0  
30775537  IMO9583615  12.9  

[30775538 rows x 7 columns]

In [3]:
%%time
#select Data for may 2019
start, end = cudf.to_datetime("2019-05-01"), cudf.to_datetime("2019-05-02")
may19 = df[(df.BaseDateTime >= start) & (df.BaseDateTime <= end)]
may19

CPU times: user 8.74 ms, sys: 6.89 ms, total: 15.6 ms
Wall time: 14.8 ms


BaseDateTime         MMSI       LAT       LON  \
3371347 2019-05-01 00:00:00  338525000.0  27.57000 -91.60783   
3371348 2019-05-01 00:05:00  338525000.0  27.57100 -91.60883   
3371349 2019-05-01 00:10:00  338525000.0  27.57256 -91.60967   
3371350 2019-05-01 00:15:00  338525000.0  27.57417 -91.61100   
3371351 2019-05-01 00:20:00  338525000.0  27.57483 -91.61182   
...                     ...          ...       ...       ...   
3417753 2019-05-02 00:00:00  538008010.0  29.31305 -94.79560   
3418033 2019-05-02 00:00:00  565155000.0  29.73971 -95.27938   
3418313 2019-05-02 00:00:00  538008025.0  29.70384 -89.98340   
3418594 2019-05-02 00:00:00  215293000.0  29.91163 -90.11215   
3418870 2019-05-02 00:00:00  255806130.0  27.90760 -89.10372   

               VesselName         IMO   SOG  
3371347   MAERSK COLUMBUS  IMO9332987   1.2  
3371348   MAERSK COLUMBUS  IMO9332987   1.1  
3371349   MAERSK COLUMBUS  IMO9332987   1.1  
3371350   MAERSK COLUMBUS  IMO9332987   1.2  
3371351   MAERSK COLUMBUS  IMO9332987   1.1  
...                   ...         ...   ...  
3417753             ASSAY  IMO9370422   0.0  
3418033   THOR FRIENDSHIP  IMO9424601   0.0  
3418313     YANGTZE CROWN  IMO9636905   0.1  
3418594  CMA CGM LA SCALA  IMO9450612   0.0  
3418870            HOLLUM  IMO9454216  11.6  

[25190 rows x 7 columns]

In [4]:
import warnings
warnings.filterwarnings('ignore')

In [24]:
%%time
# make trajectories
traj_collection = mpd.TrajectoryCollection(may19.to_pandas(), 'MMSI', t='BaseDateTime', x='LON', y='LAT', min_length=100,crs='epsg:4326')
print(f"Finished creating {len(traj_collection)} trajectories")

Finished creating 101 trajectories
CPU times: user 5.03 s, sys: 12 ms, total: 5.05 s
Wall time: 5.05 s


In [ ]:
#line trajectory
ltraj = traj_collection.to_line_gdf()
ltraj.hvplot.paths(geo=True, tiles='OSM', c='IMO')

In [9]:
%%time
plots = may19.to_pandas().hvplot.points('LON', 'LAT', geo=True, c='VesselName', alpha=0.2, tiles='ESRI')
plots.opts(opts.Overlay(title='Point data for Cargo vessels 2019-May-1'))

CPU times: user 22.8 ms, sys: 7.76 ms, total: 30.5 ms
Wall time: 30.2 ms


:Overlay
   .Tiles.I  :Tiles   [x,y]
   .Points.I :Points   [LON,LAT]   (VesselName)

In [27]:
%%time
plots = traj_collection.to_point_gdf().hvplot(geo=True, c='VesselName', alpha=0.2, tiles='ESRI')
plots.opts(opts.Overlay(title='Point data for Cargo vessels 2019-May-1'))

CPU times: user 165 ms, sys: 75 µs, total: 166 ms
Wall time: 165 ms


:Overlay
   .Tiles.I  :Tiles   [x,y]
   .Points.I :Points   [Longitude,Latitude]   (VesselName)

In [41]:
%%time
from datetime import timedelta
traj_gen = mpd.MinDistanceGeneralizer(traj_collection).generalize(tolerance=1.0)
plots = traj_gen.to_point_gdf().hvplot(geo=True, c='VesselName', alpha=0.2, tiles='ESRI')
plots.opts(opts.Overlay(title='TDTR Genralize for Cargo vessels 2019-May-1'))

CPU times: user 4.46 s, sys: 11.8 ms, total: 4.47 s
Wall time: 4.47 s


:Overlay
   .Tiles.I  :Tiles   [x,y]
   .Points.I :Points   [Longitude,Latitude]   (VesselName)

In [47]:
# tca = mpd.TrajectoryCollectionAggregator(traj_collection, max_distance=100000, min_distance=1000, min_stop_duration=360)
detector = mpd.TrajectoryStopDetector(traj_collection)
stops = detector.get_stop_points(min_duration=timedelta(seconds=3600), max_diameter=100)
stops

geometry  \
stop_id                                                       
209254000.0_2019-05-01 09:35:00  POINT (-88.94270 28.11443)   
210279000.0_2019-05-01 00:00:00  POINT (-90.01983 29.78503)   
210728000.0_2019-05-01 00:00:00  POINT (-90.11217 29.91183)   
210895000.0_2019-05-01 00:00:00  POINT (-89.81657 29.58283)   
215293000.0_2019-05-01 20:30:00  POINT (-90.11197 29.91160)   
...                                                     ...   
636092406.0_2019-05-01 00:00:00  POINT (-88.08208 30.08472)   
636092406.0_2019-05-01 01:40:00  POINT (-88.08134 30.08523)   
636092406.0_2019-05-01 05:10:00  POINT (-88.08022 30.08522)   
636092406.0_2019-05-01 09:55:00  POINT (-88.07895 30.08072)   
636092406.0_2019-05-01 18:40:00  POINT (-88.03912 30.70325)   

                                         start_time            end_time  \
stop_id                                                                   
209254000.0_2019-05-01 09:35:00 2019-05-01 09:35:00 2019-05-01 13:15:00   
210279000.0_2019-05-01 00:00:00 2019-05-01 00:00:00 2019-05-02 00:00:00   
210728000.0_2019-05-01 00:00:00 2019-05-01 00:00:00 2019-05-01 19:55:00   
210895000.0_2019-05-01 00:00:00 2019-05-01 00:00:00 2019-05-02 00:00:00   
215293000.0_2019-05-01 20:30:00 2019-05-01 20:30:00 2019-05-02 00:00:00   
...                                             ...                 ...   
636092406.0_2019-05-01 00:00:00 2019-05-01 00:00:00 2019-05-01 01:30:00   
636092406.0_2019-05-01 01:40:00 2019-05-01 01:40:00 2019-05-01 05:00:00   
636092406.0_2019-05-01 05:10:00 2019-05-01 05:10:00 2019-05-01 06:45:00   
636092406.0_2019-05-01 09:55:00 2019-05-01 09:55:00 2019-05-01 11:05:00   
636092406.0_2019-05-01 18:40:00 2019-05-01 18:40:00 2019-05-02 00:00:00   

                                     traj_id  duration_s  
stop_id                                                   
209254000.0_2019-05-01 09:35:00  209254000.0     13200.0  
210279000.0_2019-05-01 00:00:00  210279000.0     86400.0  
210728000.0_2019-05-01 00:00:00  210728000.0     71700.0  
210895000.0_2019-05-01 00:00:00  210895000.0     86400.0  
215293000.0_2019-05-01 20:30:00  215293000.0     12600.0  
...                                      ...         ...  
636092406.0_2019-05-01 00:00:00  636092406.0      5400.0  
636092406.0_2019-05-01 01:40:00  636092406.0     12000.0  
636092406.0_2019-05-01 05:10:00  636092406.0      5700.0  
636092406.0_2019-05-01 09:55:00  636092406.0      4200.0  
636092406.0_2019-05-01 18:40:00  636092406.0     19200.0  

[118 rows x 5 columns]

In [51]:
plots = stops.hvplot(geo=True, c='duration_s', alpha=0.8, tiles='ESRI', cmap="RdYlGn_r")
plots.opts(opts.Overlay(title='Stops in seconds for Cargo vessels 2019-May-1'))

:Overlay
   .Tiles.I  :Tiles   [x,y]
   .Points.I :Points   [Longitude,Latitude]   (duration_s)

In [126]:
sog = may19[may19.SOG > 0].to_pandas().hvplot(x='BaseDateTime', y='SOG')
sog

:Curve   [BaseDateTime]   (SOG)

In [127]:
may19[may19.SOG > 100]

BaseDateTime         MMSI       LAT       LON VesselName  \
3385969 2019-05-01 10:25:00  636016419.0  27.81467 -97.39888   HARRIETT   

                IMO    SOG  
3385969  IMO9239458  102.3

In [135]:
%%time
plots = may19[may19.VesselName == "HARRIETT"].to_pandas().hvplot.points('LON', 'LAT', geo=True, c='SOG', alpha=0.8, tiles='ESRI', width=1000, height=500)
plots.opts(opts.Overlay(title='Point data for Cargo vessel "HARRIETT" 2019-May-1'))

CPU times: user 10.2 ms, sys: 11.9 ms, total: 22.1 ms
Wall time: 22.9 ms


:Overlay
   .Tiles.I  :Tiles   [x,y]
   .Points.I :Points   [LON,LAT]   (SOG)

In [137]:
traj_collection.to_traj_gdf()

traj_id             start_t      end_t  \
0    209254000.0 2019-05-01 00:00:00 2019-05-02   
1    210279000.0 2019-05-01 00:00:00 2019-05-02   
2    210728000.0 2019-05-01 00:00:00 2019-05-02   
3    210895000.0 2019-05-01 00:00:00 2019-05-02   
4    215293000.0 2019-05-01 00:00:00 2019-05-02   
..           ...                 ...        ...   
96   636018581.0 2019-05-01 00:00:00 2019-05-02   
97   636091116.0 2019-05-01 14:10:00 2019-05-02   
98   636092044.0 2019-05-01 00:00:00 2019-05-02   
99   636092140.0 2019-05-01 00:00:00 2019-05-02   
100  636092406.0 2019-05-01 00:00:00 2019-05-02   

                                              geometry         length  \
0    LINESTRING (-89.01809 28.04522, -89.01739 28.0...   23498.169324   
1    LINESTRING (-90.01983 29.78503, -90.01978 29.7...    2877.755303   
2    LINESTRING (-90.11217 29.91183, -90.11225 29.9...  112682.146392   
3    LINESTRING (-89.81657 29.58283, -89.81653 29.5...    2029.695815   
4    LINESTRING (-88.48220 29.60625, -88.48805 29.5...  351290.902432   
..                                                 ...            ...   
96   LINESTRING (-89.98944 29.84242, -89.98948 29.8...    2150.198261   
97   LINESTRING (-96.13507 25.08367, -96.12705 25.0...  229755.745371   
98   LINESTRING (-88.03643 30.70541, -88.03641 30.7...    1143.414144   
99   LINESTRING (-92.93373 28.24802, -92.91688 28.2...  577586.578687   
100  LINESTRING (-88.08208 30.08472, -88.08200 30.0...   74354.506930   

      direction  
0     49.224994  
1    135.872368  
2    137.969421  
3    106.038573  
4    282.582346  
..          ...  
96   143.369786  
97    29.690746  
98   127.788932  
99    57.611309  
100    3.412654  

[101 rows x 6 columns]